In [1]:
!pip install rapidfuzz


[notice] A new release of pip is available: 23.2.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd
import requests
import time
from rapidfuzz.fuzz import ratio
from rapidfuzz import process
import re
import os


# GOOGLE COLAB

In [ ]:
# from google.colab import drive

# drive.mount('/content/drive')

In [4]:
# from google.colab import files

In [ ]:
# ruta_data_set = '/content/drive/MyDrive/Xinergy/Proyecto_homologacion_autos/database.xlsx'
# df = pd.read_excel(ruta_data_set, sheet_name='Anexo 6')
# df.head()
# df

# Local Machine

In [29]:
# Local file path (adjust path as needed)
file_path = "F:\DOCUMENTS\Xinergy\Proyecto Homologacion autos\Oficial_Resultados\Trozos\Trozo6\chunk_6.xlsx"

# Read the Excel file
df = pd.read_excel(file_path)

print(df.head())  # Display the first few rows

   Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio    plate  \
0         NaN   727782          Auto 2024-08-14 12:27:43  JJW6443   
1         NaN   727785          Auto 2024-08-14 12:29:13  EME570A   
2         NaN   727788          Auto 2024-08-14 12:30:16  DYL690B   
3         NaN   727790          Auto 2024-08-14 12:32:17  PLV083D   
4         NaN   727792          Auto 2024-08-14 12:33:49   p31bhb   

                       serie   model Tipo de Auto   car_brand    car_model  \
0          VF1LM1HM19R578307  2009.0     estandar     RENAULT    MEGANE II   
1          1B3ES56C65D119445  2005.0     estandar  FRONTERIZO  AUTOMOVILES   
2          2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO  AUTOMOVILES   
3          1B3DL46Y74N244297  2004.0     estandar       Dodge      STRATUS   
4  3G1MA5E26ML108341          2021.0     estandar   CHEVROLET         ONIX   

  car_type  Peso kg        clean_serie  clean_serie_length  
0     Auto      NaN  VF1LM1HM19R578307                 

# Cleaning and preparing

In [30]:
df["clean_serie"] = (
    df["serie"]
    .fillna("")  # Replace NaN with an empty string
    .astype(str)  # Ensure all entries are strings
    .str.strip()  # Remove leading and trailing whitespaces
    .str.replace(r"[$]+$", "", regex=True)  # Remove trailing "$"
    .str.replace(r"[^\w\s]", "", regex=True)  # Remove punctuation
)

In [31]:
df

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model car_type  Peso kg        clean_serie  clean_serie_length  
0        MEGANE II     Auto      NaN  VF1LM1HM19R578307                  17  
1      AUTOMOVILES     Auto      NaN  1B3ES56C65D119445                  17  
2      AUTOMOVILES     Auto      NaN  2FMDK49C27BB06244                  17  
3          STRATUS     Auto      NaN  1B3DL46Y74N244297                  17  
4             ONIX     Auto      NaN  3G1MA5E26ML108341                  17  
...            ...      ...      ...                ...                 ...  
39995          i10      NaN      NaN  MALB24BC2PM168319                  17  
39996            5      NaN      NaN  LSJA36E9XRZ053222                  17  
39997        VENTO      NaN      NaN  MEX5J2605JT028891                  17  
39998         CITY      NaN      NaN  93HGM2640AZ805809                  17  
39999        VENTO      NaN      NaN  MEX3G2607ET011196                  17  

[40000 rows x 14 columns]

In [32]:
# Add a new column that counts the number of characters in 'clean_serie'
df["clean_serie_length"] = df["clean_serie"].apply(len)


In [33]:
# Count rows where "clean_serie_length" equals 17
count_17 = (df["clean_serie_length"] == 17).sum()

print(f"Number of rows with value 17 in 'clean_serie_length': {count_17}")


Number of rows with value 17 in 'clean_serie_length': 40000


In [34]:
# Randomly selects 1,000 rows
#df2 = df[df["clean_serie_length"] == 17].sample(n=1000, random_state=40).copy()

#The HOLE dataframe
df2 = df[df["clean_serie_length"] == 17].copy()  # Create a deep copy


In [35]:
df2

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model car_type  Peso kg        clean_serie  clean_serie_length  
0        MEGANE II     Auto      NaN  VF1LM1HM19R578307                  17  
1      AUTOMOVILES     Auto      NaN  1B3ES56C65D119445                  17  
2      AUTOMOVILES     Auto      NaN  2FMDK49C27BB06244                  17  
3          STRATUS     Auto      NaN  1B3DL46Y74N244297                  17  
4             ONIX     Auto      NaN  3G1MA5E26ML108341                  17  
...            ...      ...      ...                ...                 ...  
39995          i10      NaN      NaN  MALB24BC2PM168319                  17  
39996            5      NaN      NaN  LSJA36E9XRZ053222                  17  
39997        VENTO      NaN      NaN  MEX5J2605JT028891                  17  
39998         CITY      NaN      NaN  93HGM2640AZ805809                  17  
39999        VENTO      NaN      NaN  MEX3G2607ET011196                  17  

[40000 rows x 14 columns]

In [36]:
# Add the new columns without warnings
df2["Maker_api"] = None
df2["Model_api"] = None
df2["Type_api"] = None
df2["Weight_api"] = None

In [37]:
df2

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model car_type  Peso kg        clean_serie  clean_serie_length  \
0        MEGANE II     Auto      NaN  VF1LM1HM19R578307                  17   
1      AUTOMOVILES     Auto      NaN  1B3ES56C65D119445                  17   
2      AUTOMOVILES     Auto      NaN  2FMDK49C27BB06244                  17   
3          STRATUS     Auto      NaN  1B3DL46Y74N244297                  17   
4             ONIX     Auto      NaN  3G1MA5E26ML108341                  17   
...            ...      ...      ...                ...                 ...   
39995          i10      NaN      NaN  MALB24BC2PM168319                  17   
39996            5      NaN      NaN  LSJA36E9XRZ053222                  17   
39997        VENTO      NaN      NaN  MEX5J2605JT028891                  17   
39998         CITY      NaN      NaN  93HGM2640AZ805809                  17   
39999        VENTO      NaN      NaN  MEX3G2607ET011196                  17   

      Maker_api Model_api Type_api Weight_api  
0          None      None     None       None  
1          None      None     None       None  
2          None      None     None       None  
3          None      None     None       None  
4          None      None     None       None  
...         ...       ...      ...        ...  
39995      None      None     None       None  
39996      None      None     None       None  
39997      None      None     None       None  
39998      None      None     None       None  
39999      None      None     None       None  

[40000 rows x 18 columns]

In [38]:
# API Function
def get_vehicle_info(vin):
    """
    Fetches the maker, model, weight, and vehicle type for a given VIN using the NHTSA API in a single request.

    Parameters:
    vin (str): The VIN of the vehicle.

    Returns:
    dict: A dictionary containing 'Maker', 'Model', 'Weight', and 'Vehicle Type' keys with their corresponding values, or None if not found.
    """
    url = f"https://vpic.nhtsa.dot.gov/api/vehicles/DecodeVin/{vin}?format=json"
    try:
        response = requests.get(url)
        if response.status_code == 200:
            results = response.json().get("Results", [])
            maker = None
            model = None
            vehicle_type = None
            weight = None

            # Loop through results to extract relevant data
            for item in results:
                if item["Variable"] == "Make" and item["Value"]:
                    maker = item["Value"]
                elif item["Variable"] == "Model" and item["Value"]:
                    model = item["Value"]
                elif item["Variable"] == "Vehicle Type" and item["Value"]:
                    vehicle_type = item["Value"]
                elif item["Variable"] == "Gross Vehicle Weight Rating From" and item["Value"]:
                    weight = item["Value"]

            return {
                "Maker": maker,
                "Model": model,
                "Vehicle Type": vehicle_type,
                "Weight": weight
            }

        return None  # Return None if the API call is unsuccessful
    except Exception as e:
        print(f"Error for VIN {vin}: {e}")
        return None


In [39]:
# Save progress every BATCH_SIZE rows
BATCH_SIZE = 5000

#GOOGLE COlab
# OUTPUT_FILE = "/content/drive/MyDrive/Xinergy/Proyecto_homologacion_autos/BATCHES/vehicle_info_progress.xlsx"
# BATCH_OUTPUT_TEMPLATE = "/content/drive/MyDrive/Xinergy/Proyecto_homologacion_autos/BATCHES/vehicle_info_batch_{batch_num}.xlsx"

#LOCAL MACHINE
OUTPUT_FILE = r"F:\DOCUMENTS\Xinergy\Proyecto Homologacion autos\Oficial_Resultados\Trozos\Trozo6\vehicle_info_progress.xlsx"
BATCH_OUTPUT_TEMPLATE = r"F:\DOCUMENTS\Xinergy\Proyecto Homologacion autos\Oficial_Resultados\Trozos\Trozo6\BATCHES\vehicle_info_batch_{batch_num}.xlsx"


# Reload progress if the file exists
try:
    progress_df = pd.read_excel(OUTPUT_FILE)
    print(f"Loaded progress from {OUTPUT_FILE}")

    # Merge progress with the original DataFrame
    df2 = df2.merge(progress_df, how="left", on="clean_serie", suffixes=("", "_progress"))

    # Fill columns from progress
    for col in ["Maker_api", "Model_api", "Type_api", "Weight_api"]:
        df2[col] = df2[f"{col}_progress"].combine_first(df2[col])

    # Drop extra columns created during merging
    df2 = df2.drop(columns=[col for col in df2.columns if col.endswith("_progress")])

except FileNotFoundError:
    print(f"No progress file found. Starting fresh.")

# Initialize batch counter and processed row counter
batch_counter = 1
processed_count = 0



No progress file found. Starting fresh.


In [40]:
# Iterate through DataFrame
for index, row in df2.iterrows():
    # Skip already processed rows
    if pd.notnull(row.get("Maker_api")):
        continue

    vin = row["clean_serie"]

    if len(vin) != 17:  # Skip rows where VIN is not 17 characters
        continue

    # Fetch all vehicle information in a single API call
    vehicle_info = get_vehicle_info(vin)

    if vehicle_info:
        # Update respective columns with fetched information in lowercase
        df2.at[index, "Maker_api"] = vehicle_info["Maker"].lower() if vehicle_info["Maker"] else None
        df2.at[index, "Model_api"] = vehicle_info["Model"].lower() if vehicle_info["Model"] else None
        df2.at[index, "Type_api"] = vehicle_info["Vehicle Type"].lower() if vehicle_info["Vehicle Type"] else None
        df2.at[index, "Weight_api"] = vehicle_info["Weight"].lower() if vehicle_info["Weight"] else None

        print(f"Processed VIN {index}: {vin} -> Maker: {vehicle_info['Maker']}, Model: {vehicle_info['Model']}, Vehicle Type: {vehicle_info['Vehicle Type']} Weight: {vehicle_info['Weight']}")
    else:
        print(f"Failed to retrieve data for VIN {index}: {vin}")

    # Increment processed count
    processed_count += 1

    # Save progress every BATCH_SIZE processed rows
    if processed_count % BATCH_SIZE == 0:
        # Save cumulative progress
        df2.to_excel(OUTPUT_FILE, index=False)
        print(f"Cumulative progress saved to {OUTPUT_FILE}")

        # Save batch progress to a separate file
        batch_output_file = BATCH_OUTPUT_TEMPLATE.format(batch_num=batch_counter)
        df2.iloc[:index + 1].to_excel(batch_output_file, index=False)
        print(f"\nBatch {batch_counter} progress saved to {batch_output_file}\n")

        # Increment batch counter
        batch_counter += 1

    # Add a delay to respect API rate limits
    time.sleep(0.1)

# Final save after loop completion
df2.to_excel(OUTPUT_FILE, index=False)
print(f"Processing complete. Final progress saved to {OUTPUT_FILE}")


Processed VIN 0: VF1LM1HM19R578307 -> Maker: EAGLE, Model: None, Vehicle Type: PASSENGER CAR Weight: None
Processed VIN 1: 1B3ES56C65D119445 -> Maker: DODGE, Model: Neon, Vehicle Type: PASSENGER CAR Weight: Class 1: 6,000 lb or less (2,722 kg or less)
Processed VIN 2: 2FMDK49C27BB06244 -> Maker: FORD, Model: Edge, Vehicle Type: MULTIPURPOSE PASSENGER VEHICLE (MPV) Weight: Class 1D: 5,001 - 6,000 lb (2,268 - 2,722 kg)
Processed VIN 3: 1B3DL46Y74N244297 -> Maker: DODGE, Model: Stratus, Vehicle Type: PASSENGER CAR Weight: Class 1: 6,000 lb or less (2,722 kg or less)
Processed VIN 4: 3G1MA5E26ML108341 -> Maker: CHEVROLET, Model: Onix, Vehicle Type: PASSENGER CAR Weight: None
Processed VIN 5: JTFSX23P4J6184843 -> Maker: None, Model: None, Vehicle Type: None Weight: None
Processed VIN 6: 3N1CN7AD2KK408796 -> Maker: NISSAN, Model: Versa, Vehicle Type: PASSENGER CAR Weight: Class 1: 6,000 lb or less (2,722 kg or less)
Processed VIN 7: 3VVHP65N8JM076281 -> Maker: VOLKSWAGEN, Model: None, Vehicl

In [41]:
df2

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model car_type  Peso kg        clean_serie  clean_serie_length  \
0        MEGANE II     Auto      NaN  VF1LM1HM19R578307                  17   
1      AUTOMOVILES     Auto      NaN  1B3ES56C65D119445                  17   
2      AUTOMOVILES     Auto      NaN  2FMDK49C27BB06244                  17   
3          STRATUS     Auto      NaN  1B3DL46Y74N244297                  17   
4             ONIX     Auto      NaN  3G1MA5E26ML108341                  17   
...            ...      ...      ...                ...                 ...   
39995          i10      NaN      NaN  MALB24BC2PM168319                  17   
39996            5      NaN      NaN  LSJA36E9XRZ053222                  17   
39997        VENTO      NaN      NaN  MEX5J2605JT028891                  17   
39998         CITY      NaN      NaN  93HGM2640AZ805809                  17   
39999        VENTO      NaN      NaN  MEX3G2607ET011196                  17   

       Maker_api Model_api                              Type_api  \
0          eagle      None                         passenger car   
1          dodge      neon                         passenger car   
2           ford      edge  multipurpose passenger vehicle (mpv)   
3          dodge   stratus                         passenger car   
4      chevrolet      onix                         passenger car   
...          ...       ...                                   ...   
39995       None      None                                  None   
39996       None      None                                  None   
39997       None      None                                  None   
39998       None      None                                  None   
39999       None      None                                  None   

                                          Weight_api  
0                                               None  
1       class 1: 6,000 lb or less (2,722 kg or less)  
2      class 1d: 5,001 - 6,000 lb (2,268 - 2,722 kg)  
3       class 1: 6,000 lb or less (2,722 kg or less)  
4                                               None  
...                                              ...  
39995                                           None  
39996                                           None  
39997           

In [42]:
df3 = df2.copy() #Copiar el dataframe con los resultados de la API

In [43]:
df3

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model car_type  Peso kg        clean_serie  clean_serie_length  \
0        MEGANE II     Auto      NaN  VF1LM1HM19R578307                  17   
1      AUTOMOVILES     Auto      NaN  1B3ES56C65D119445                  17   
2      AUTOMOVILES     Auto      NaN  2FMDK49C27BB06244                  17   
3          STRATUS     Auto      NaN  1B3DL46Y74N244297                  17   
4             ONIX     Auto      NaN  3G1MA5E26ML108341                  17   
...            ...      ...      ...                ...                 ...   
39995          i10      NaN      NaN  MALB24BC2PM168319                  17   
39996            5      NaN      NaN  LSJA36E9XRZ053222                  17   
39997        VENTO      NaN      NaN  MEX5J2605JT028891                  17   
39998         CITY      NaN      NaN  93HGM2640AZ805809                  17   
39999        VENTO      NaN      NaN  MEX3G2607ET011196                  17   

       Maker_api Model_api                              Type_api  \
0          eagle      None                         passenger car   
1          dodge      neon                         passenger car   
2           ford      edge  multipurpose passenger vehicle (mpv)   
3          dodge   stratus                         passenger car   
4      chevrolet      onix                         passenger car   
...          ...       ...                                   ...   
39995       None      None                                  None   
39996       None      None                                  None   
39997       None      None                                  None   
39998       None      None                                  None   
39999       None      None                                  None   

                                          Weight_api  
0                                               None  
1       class 1: 6,000 lb or less (2,722 kg or less)  
2      class 1d: 5,001 - 6,000 lb (2,268 - 2,722 kg)  
3       class 1: 6,000 lb or less (2,722 kg or less)  
4                                               None  
...                                              ...  
39995                                           None  
39996                                           None  
39997           

# Etapa de estandarización de marca y modelo

In [44]:
df3["clean_car_maker"] = (
    df3["car_brand"]
    .fillna("")  # Replace NaN with an empty string
    .astype(str)  # Ensure all values are strings
    .str.lower()  # Convert all strings to lowercase
    .str.replace(r'[^a-z0-9 ]', '', regex=True)  # Remove only special characters
    .str.strip()  # Remove leading and trailing spaces
)

df3["clean_car_model"] = (
    df3["car_model"]
    .fillna("")  # Replace NaN with an empty string
    .astype(str)  # Ensure all values are strings
    .str.lower()  # Convert all strings to lowercase
    .str.strip()  # Remove leading and trailing spaces
)

In [45]:
df3["Maker_final"] = None
df3["Maker_Similarity_score"] = None

df3["Model_final"] = None
df3["Model_Similarity_score"] = None

In [46]:
df3

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model  ...  Maker_api  Model_api  \
0        MEGANE II  ...      eagle       None   
1      AUTOMOVILES  ...      dodge       neon   
2      AUTOMOVILES  ...       ford       edge   
3          STRATUS  ...      dodge    stratus   
4             ONIX  ...  chevrolet       onix   
...            ...  ...        ...        ...   
39995          i10  ...       None       None   
39996            5  ...       None       None   
39997        VENTO  ...       None       None   
39998         CITY  ...       None       None   
39999        VENTO  ...       None       None   

                                   Type_api  \
0                             passenger car   
1                             passenger car   
2      multipurpose passenger vehicle (mpv)   
3                             passenger car   
4                             passenger car   
...                                     ...   
39995                                  None   
39996                                  None   
39997                                  None   
39998                                  None   
39999                                  None   

                                          Weight_api clean_car_maker  \
0                                               None         renault   
1       class 1: 6,000 lb or less (2,722 kg or less)      fronterizo   
2      class 1d: 5,001 - 6,000 lb (2,268 - 2,722 kg)      fronterizo   
3       class 1: 6,000 lb or less (2,722 kg or less)           dodge   
4                                               None       chevrolet   
...                                              ...             ...   
39995                                           None         hyundai   
39996                                           None              mg   
39997                                           None      volkswagen   
39998                                           None           honda   
39999                                           None      volkswagen   

      clean_car_model Maker_final Maker_Similarity_score Model_final  \
0           megane ii        None                   None        None   
1         automoviles        None                   None        None   
2         automoviles        None         

In [47]:
#maker_api_set = set(df2["Maker_api"].dropna())

mode_api_set = set(df3["Model_api"].dropna())

car_makers = set([
    "acura", "alfa romeo", "audi", "baic", "bajaj", "bentley", "bmw", "buick",
    "byd", "cadillac", "chevrolet", "changan", "chery", "chrysler", "cupra", "daewoo",
    "dodge", "ducati", "fiat", "ford", "foton", "freightliner", "gmc", "great wall",
    "haval", "harley", "hino", "honda", "hummer", "hyundai", "infiniti", "isuzu",
    "italika", "jac", "jaguar", "jeep", "jmc", "kenworth", "kia", "kurazai",
    "land rover", "lexus", "lincoln", "mack", "masserati", "mazda", "mercedes-benz", "mercedes benz",
    "mg", "mini", "mitsubishi", "nissan", "peugeot", "peterbilt", "piaggio", "pontiac", "plymouth",
    "porsche", "ram", "renault", "saab", "scania", "seat", "sinotruk", "subaru",
    "suzuki", "tesla", "tiggo", "toyota", "volkswagen", "volvo", "yamaha", "vento",
    "kawazaki", "ktm", "aprilia", "bimota", "mv agusta", "royal enfield",
    "harley-davidson", "hero", "husqvarna", "indian", "vespa", "zanella", "benelli",
    "cf moto", "kymco", "norton", "sym", "lotus", "citroen", "dacia", "opel", "skoda",
    "smart", "tata", "mahindra", "geely", "proton", "lada", "ssangyong", "maruti",
    "chrysler", "saturn", "daewoo", "saic", "zhongxing", "haima", "reno", "vw", "ram"
])

In [48]:
def car_maker(maker_api, clean_car_brand, list_errors, car_makers, min_value_fuzz_score=60):
    """
    Processes car maker information for a single row.

    Parameters:
    - maker_api (str): Value from the "Maker_api" column.
    - clean_car_brand (str): Value from the "clean_car_brand" column.
    - list_errors (list): List of error strings to clean.
    - car_makers (set): Set of standardized car makers for matching.
    - min_value_fuzz_score (int): Minimum fuzz score for matching.

    Returns:
    - dict: A dictionary with 'Maker_final' and 'Maker_Similarity_score'.
    """
    # Initialize default result
    result = {"Maker_final": "N/A", "Maker_Similarity_score": 0}

    # Case 1: No value in "clean_car_brand" but value in "Maker_api"
    if pd.isna(clean_car_brand) and pd.notna(maker_api):
        result["Maker_final"] = maker_api
        return result  # Exit early like "continue"

    # Case 2: Value in "clean_car_brand" but no value in "Maker_api"
    if pd.notna(clean_car_brand) and pd.isna(maker_api):
        # Remove error strings from "clean_car_brand"
        clean_brand_without_errors = clean_car_brand.lower()
        for error in list_errors:
            clean_brand_without_errors = clean_brand_without_errors.replace(error, "").strip()

        if clean_brand_without_errors == "":
            result["Maker_final"] = "N/A caso 2.0"
            return result  # Exit early like "continue"

        # Find the best match for "clean_car_brand" in the "car_makers" set
        result_match = process.extractOne(clean_brand_without_errors, car_makers, scorer=ratio)
        if result_match:
            best_match, best_score, _ = result_match
            if best_score >= min_value_fuzz_score:
                result["Maker_final"] = best_match
                result["Maker_Similarity_score"] = best_score
            else:
                result["Maker_final"] = "N/A caso 2.1"
        else:
            result["Maker_final"] = "N/A caso 2.2"
        return result  # Exit early like "continue"

    # Case 3: Both "clean_car_brand" and "Maker_api" have values
    if pd.notna(clean_car_brand) and pd.notna(maker_api):
        # Remove error strings from "clean_car_brand"
        clean_brand_without_errors = clean_car_brand.lower()
        for error in list_errors:
            clean_brand_without_errors = clean_brand_without_errors.replace(error, "").strip()

        if clean_brand_without_errors == "":
            result["Maker_final"] = maker_api
            return result  # Exit early like "continue"

        # Calculate the fuzz ratio with the cleaned brand
        fuzz_score = ratio(clean_brand_without_errors, maker_api)
        result["Maker_Similarity_score"] = fuzz_score

        # Set "Maker_final" based on the fuzz score
        if fuzz_score >= min_value_fuzz_score:
            result["Maker_final"] = maker_api
        else:
            result["Maker_final"] = "N/A caso 3"

    return result


In [49]:
def car_model(model_api, clean_car_model, maker_api, list_errors, min_value_fuzz_score=60):
    """
    Processes car model information for a single row.

    Parameters:
    - model_api (str): Value from the "Model_api" column.
    - clean_car_model (str): Value from the "clean_car_model" column.
    - maker_api (str): Value from the "Maker_api" column to handle maker-related logic.
    - list_errors (list): List of error strings to clean.
    - min_value_fuzz_score (int): Minimum fuzz score for matching.

    Returns:
    - dict: A dictionary with 'Model_final' and 'Model_Similarity_score'.
    """
    # Initialize default result
    result = {"Model_final": "N/A", "Model_Similarity_score": 0}

    # Case 1: No value in "clean_car_model" but value in "model_api"
    if pd.isna(clean_car_model) and pd.notna(model_api):
        result["Model_final"] = model_api
        return result  # Exit early

    # Case 2: Value in "clean_car_model" but no value in "model_api"
    if pd.notna(clean_car_model) and pd.isna(model_api):
        # Remove error strings from "clean_car_model"
        clean_model_without_errors = clean_car_model.lower()
        for error in list_errors:
            clean_model_without_errors = clean_model_without_errors.replace(error, "").strip()

        # If the cleaned model is empty, return "N/A"
        if clean_model_without_errors == "":
            result["Model_final"] = "N/A case 2.0"
        else:
            result["Model_final"] = clean_model_without_errors
        return result  # Exit early

    # Case 3: Both "clean_car_model" and "model_api" have values
    if pd.notna(clean_car_model) and pd.notna(model_api):
        # If there is a value in "maker_api", set "Model_final" to "model_api"
        if pd.notna(maker_api):
            result["Model_final"] = model_api
            result["Model_Similarity_score"] = 100  # Full match since maker exists
            return result  # Exit early

        # Remove error strings from "clean_car_model"
        clean_model_without_errors = clean_car_model.lower()
        for error in list_errors:
            clean_model_without_errors = clean_model_without_errors.replace(error, "").strip()

        if clean_model_without_errors == "":
            result["Model_final"] = "N/A 3.0"
            result["Model_Similarity_score"] = 0
            return result  # Exit early

        # Calculate the fuzz ratio with the cleaned model
        fuzz_score = ratio(clean_model_without_errors, model_api)
        result["Model_Similarity_score"] = fuzz_score

        # Set "Model_final" based on the fuzz score
        if fuzz_score >= min_value_fuzz_score:
            result["Model_final"] = model_api
        else:
            result["Model_final"] = "N/A 3.1"

    return result


In [50]:
list_errors_makers = ["legalizado", "fronterizo", "especiales", "moto", "motocicletas", "turistas", "internacional", "international"]
list_errors_models = ["automoviles", "chasis", "pick up", "pickup"]

In [51]:
def process_row(row):
    maker_result = car_maker(
        maker_api=row["Maker_api"],
        clean_car_brand=row["clean_car_maker"],
        list_errors=list_errors_makers,
        car_makers=car_makers,
        min_value_fuzz_score=60
    )

    model_result = car_model(
        model_api=row["Model_api"],
        clean_car_model=row["clean_car_model"],
        maker_api=row["Maker_api"],  # Pass maker_api explicitly
        list_errors=list_errors_models,
        min_value_fuzz_score=60
    )

    return {
        "Maker_final": maker_result["Maker_final"],
        "Maker_Similarity_score": maker_result["Maker_Similarity_score"],
        "Model_final": model_result["Model_final"],
        "Model_Similarity_score": model_result["Model_Similarity_score"],
    }


# Apply the combined function to the DataFrame
results = df3.apply(process_row, axis=1)

# Unpack results into new columns in df3
df3["Maker_final"] = results.apply(lambda x: x["Maker_final"])
df3["Maker_Similarity_score"] = results.apply(lambda x: x["Maker_Similarity_score"])
df3["Model_final"] = results.apply(lambda x: x["Model_final"])
df3["Model_Similarity_score"] = results.apply(lambda x: x["Model_Similarity_score"])



In [52]:
df3

Unnamed: 0  numcaso tipo_vehiculo      fecha_servicio      plate  \
0             NaN   727782          Auto 2024-08-14 12:27:43    JJW6443   
1             NaN   727785          Auto 2024-08-14 12:29:13    EME570A   
2             NaN   727788          Auto 2024-08-14 12:30:16    DYL690B   
3             NaN   727790          Auto 2024-08-14 12:32:17    PLV083D   
4             NaN   727792          Auto 2024-08-14 12:33:49     p31bhb   
...           ...      ...           ...                 ...        ...   
39995         NaN   568666           NaN 2024-03-15 00:00:00  SHS-705-B   
39996         NaN   568675           NaN 2024-03-15 00:00:00    NAV518A   
39997         NaN   568680           NaN 2024-03-15 00:00:00     J50ARD   
39998         NaN   568685           NaN 2024-03-15 00:00:00    RML386B   
39999         NaN   568709           NaN 2024-03-15 00:00:00    UMV053E   

                           serie   model Tipo de Auto   car_brand  \
0              VF1LM1HM19R578307  2009.0     estandar     RENAULT   
1              1B3ES56C65D119445  2005.0     estandar  FRONTERIZO   
2              2FMDK49C27BB06244  2007.0     estandar  FRONTERIZO   
3              1B3DL46Y74N244297  2004.0     estandar       Dodge   
4      3G1MA5E26ML108341          2021.0     estandar   CHEVROLET   
...                          ...     ...          ...         ...   
39995          MALB24BC2PM168319  2023.0          NaN     HYUNDAI   
39996          LSJA36E9XRZ053222  2024.0          NaN          MG   
39997          MEX5J2605JT028891  2018.0          NaN  VOLKSWAGEN   
39998          93HGM2640AZ805809  2010.0          NaN       HONDA   
39999          MEX3G2607ET011196  2014.0          NaN  VOLKSWAGEN   

         car_model  ...  Maker_api  Model_api  \
0        MEGANE II  ...      eagle       None   
1      AUTOMOVILES  ...      dodge       neon   
2      AUTOMOVILES  ...       ford       edge   
3          STRATUS  ...      dodge    stratus   
4             ONIX  ...  chevrolet       onix   
...            ...  ...        ...        ...   
39995          i10  ...       None       None   
39996            5  ...       None       None   
39997        VENTO  ...       None       None   
39998         CITY  ...       None       None   
39999        VENTO  ...       None       None   

                                   Type_api  \
0                             passenger car   
1                             passenger car   
2      multipurpose passenger vehicle (mpv)   
3                             passenger car   
4                             passenger car   
...                                     ...   
39995                                  None   
39996                                  None   
39997                                  None   
39998                                  None   
39999                                  None   

                                          Weight_api clean_car_maker  \
0                                               None         renault   
1       class 1: 6,000 lb or less (2,722 kg or less)      fronterizo   
2      class 1d: 5,001 - 6,000 lb (2,268 - 2,722 kg)      fronterizo   
3       class 1: 6,000 lb or less (2,722 kg or less)           dodge   
4                                               None       chevrolet   
...                                              ...             ...   
39995                                           None         hyundai   
39996                                           None              mg   
39997                                           None      volkswagen   
39998                                           None           honda   
39999                                           None      volkswagen   

      clean_car_model Maker_final Maker_Similarity_score Model_final  \
0           megane ii  N/A caso 3                   50.0   megane ii   
1         automoviles       dodge                    0.0        neon   
2         automoviles        ford         

#Export

In [53]:
# Define the file name and path
output_file = "Trozo6.xlsx"

# Export df2 to an Excel file
df3.to_excel(output_file, index=False)

print(f"DataFrame exported successfully to {output_file}")


DataFrame exported successfully to Trozo6.xlsx
